In [1]:
import numpy as np
import requests
import pandas as pd
from my_utils import *
from tqdm import tqdm
tqdm.pandas()

In [2]:
api_key = 'RGAPI-c36f6f40-6def-40c6-8374-2b5a2bb2ecba'

In [3]:
url = 'https://kr.api.riotgames.com/lol/league/v4/entries/RANKED_SOLO_5x5/DIAMOND/I?page=1&api_key='+api_key

In [4]:
res = requests.get(url).json()

In [5]:
res[0].keys()

dict_keys(['leagueId', 'queueType', 'tier', 'rank', 'summonerId', 'summonerName', 'leaguePoints', 'wins', 'losses', 'veteran', 'inactive', 'freshBlood', 'hotStreak'])

In [6]:
summonerName_lst = list(map(lambda x: x['summonerName'], res))

In [7]:
def get_lst(summonerName_lst):
    tmp = []
    for i in summonerName_lst[:3]:
        puuid = get_puuid(i)
        matchid = get_matchid(puuid, 3)
        matchs_timelines = get_matchs_timelines(matchid)
        tmp.extend(matchs_timelines)
    return tmp

In [8]:
tmp = get_lst(summonerName_lst)

In [9]:
df = pd.DataFrame(tmp, columns = ['gameid', 'matchs', 'timelines'])

In [10]:
df

gameid                                             matchs  \
0  KR_5959757493  {'metadata': {'dataVersion': '2', 'matchId': '...   
1  KR_5959723670  {'metadata': {'dataVersion': '2', 'matchId': '...   
2  KR_5959674785  {'metadata': {'dataVersion': '2', 'matchId': '...   
3  KR_6011052920  {'metadata': {'dataVersion': '2', 'matchId': '...   
4  KR_6010996212  {'metadata': {'dataVersion': '2', 'matchId': '...   
5  KR_6010990529  {'metadata': {'dataVersion': '2', 'matchId': '...   
6  KR_6007125879  {'metadata': {'dataVersion': '2', 'matchId': '...   
7  KR_6007054592  {'metadata': {'dataVersion': '2', 'matchId': '...   
8  KR_6005739151  {'metadata': {'dataVersion': '2', 'matchId': '...   

                                           timelines  
0  {'metadata': {'dataVersion': '2', 'matchId': '...  
1  {'metadata': {'dataVersion': '2', 'matchId': '...  
2  {'metadata': {'dataVersion': '2', 'matchId': '...  
3  {'metadata': {'dataVersion': '2', 'matchId': '...  
4  {'metadata': {'dataVersion': '2', 'matchId': '...  
5  {'metadata': {'dataVersion': '2', 'matchId': '...  
6  {'metadata': {'dataVersion': '2', 'matchId': '...  
7  {'metadata': {'dataVersion': '2', 'matchId': '...  
8  {'metadata': {'dataVersion': '2', 'matchId': '...

In [12]:
df.iloc[0].matchs['info']['teams'][0].keys()

dict_keys(['bans', 'objectives', 'teamId', 'win'])

In [13]:
df.iloc[0].matchs['info']['teams'][0]['teamId']

100

In [14]:
df.iloc[0].matchs['info']['teams'][0]

{'bans': [{'championId': 55, 'pickTurn': 1},
  {'championId': -1, 'pickTurn': 2},
  {'championId': 62, 'pickTurn': 3},
  {'championId': 53, 'pickTurn': 4},
  {'championId': 7, 'pickTurn': 5}],
 'objectives': {'baron': {'first': False, 'kills': 0},
  'champion': {'first': False, 'kills': 18},
  'dragon': {'first': False, 'kills': 0},
  'inhibitor': {'first': False, 'kills': 0},
  'riftHerald': {'first': False, 'kills': 1},
  'tower': {'first': False, 'kills': 2}},
 'teamId': 100,
 'win': False}

In [15]:
df.iloc[0].matchs['info']['teams'][0]['bans'][0]

{'championId': 55, 'pickTurn': 1}

In [16]:
len(df.iloc[0].matchs['info']['teams'])

2

In [17]:
len(df.iloc[0].matchs['info']['teams'][0]['bans'])

5

In [18]:
def ban_lst(x):
    lst = []
    for i in x.matchs['info']['teams']:
        for j in i['bans']:
            lst.append(j['championId'])
    return lst

In [19]:
ban = df.apply(lambda x: ban_lst(x), axis = 1)

In [20]:
ban

0            [55, -1, 62, 53, 7, -1, 58, 221, 41, -1]
1        [203, 7, 235, 96, -1, 236, 517, 234, 68, 53]
2      [234, 163, 236, 203, -1, 221, 7, 350, 55, 238]
3     [421, 221, 517, 103, 39, 62, 28, 555, 421, 221]
4    [360, 268, 111, 114, 22, 421, 555, 127, 53, 164]
5      [62, 24, 81, 421, 888, 111, 62, 235, 421, 142]
6                                                  []
7                                                  []
8                                                  []
dtype: object

-------------------------------------------------------------------------------------

In [21]:
blue_ban = list(map(lambda x: str(x['championId']), df.iloc[0].matchs['info']['teams'][0]['bans']))

In [22]:
blue_ban

['55', '-1', '62', '53', '7']

In [23]:
red_ban = list(map(lambda x: str(x['championId']), df.iloc[0].matchs['info']['teams'][1]['bans']))

In [24]:
red_ban

['-1', '58', '221', '41', '-1']

In [25]:
ban_tmp = list(set(blue_ban + red_ban))

In [26]:
'|'.join(ban_tmp)

'55|41|62|7|221|58|53|-1'

In [27]:
df.iloc[0].timelines['info'].keys()

dict_keys(['frameInterval', 'frames', 'gameId', 'participants'])

In [28]:
df.iloc[0].timelines['info']['frames']

[{'events': [{'realTimestamp': 1654773145487,
    'timestamp': 0,
    'type': 'PAUSE_END'}],
  'participantFrames': {'1': {'championStats': {'abilityHaste': 0,
     'abilityPower': 0,
     'armor': 33,
     'armorPen': 0,
     'armorPenPercent': 0,
     'attackDamage': 25,
     'attackSpeed': 100,
     'bonusArmorPenPercent': 0,
     'bonusMagicPenPercent': 0,
     'ccReduction': 0,
     'cooldownReduction': 0,
     'health': 625,
     'healthMax': 625,
     'healthRegen': 0,
     'lifesteal': 0,
     'magicPen': 0,
     'magicPenPercent': 0,
     'magicResist': 32,
     'movementSpeed': 340,
     'omnivamp': 0,
     'physicalVamp': 0,
     'power': 325,
     'powerMax': 325,
     'powerRegen': 0,
     'spellVamp': 0},
    'currentGold': 500,
    'damageStats': {'magicDamageDone': 0,
     'magicDamageDoneToChampions': 0,
     'magicDamageTaken': 0,
     'physicalDamageDone': 0,
     'physicalDamageDoneToChampions': 0,
     'physicalDamageTaken': 0,
     'totalDamageDone': 0,
     'tota

In [29]:
df.iloc[0].timelines['info']['frames'][11]

{'events': [{'itemId': 1052,
   'participantId': 4,
   'timestamp': 600704,
   'type': 'ITEM_DESTROYED'},
  {'itemId': 3802,
   'participantId': 4,
   'timestamp': 600704,
   'type': 'ITEM_PURCHASED'},
  {'itemId': 1001,
   'participantId': 4,
   'timestamp': 602389,
   'type': 'ITEM_PURCHASED'},
  {'itemId': 1036,
   'participantId': 5,
   'timestamp': 602653,
   'type': 'ITEM_DESTROYED'},
  {'itemId': 1036,
   'participantId': 5,
   'timestamp': 602653,
   'type': 'ITEM_DESTROYED'},
  {'itemId': 3134,
   'participantId': 5,
   'timestamp': 602653,
   'type': 'ITEM_PURCHASED'},
  {'itemId': 1001,
   'participantId': 5,
   'timestamp': 606057,
   'type': 'ITEM_DESTROYED'},
  {'itemId': 3009,
   'participantId': 5,
   'timestamp': 606057,
   'type': 'ITEM_PURCHASED'},
  {'level': 9, 'participantId': 8, 'timestamp': 606389, 'type': 'LEVEL_UP'},
  {'levelUpType': 'NORMAL',
   'participantId': 8,
   'skillSlot': 1,
   'timestamp': 607049,
   'type': 'SKILL_LEVEL_UP'},
  {'itemId': 1036,
  

In [30]:
def log_lst(x):
    lst = []
    for i in x.timelines['info']['frames']:
        for j in i['events']:
            if j['type'] == 'CHAMPION_KILL':
                lst.append(j['killerId'])
                lst.append(j['victimId'])
                try:
                    lst.append(j['assistingParticipantIds'])
                except:
                    lst.append(-1)
    return lst

In [31]:
log = df.apply(lambda x: log_lst(x), axis = 1)

In [32]:
log

0    [6, 3, -1, 2, 10, [4, 5], 3, 9, -1, 9, 2, -1, ...
1    [7, 5, [9, 10], 10, 4, [7, 9], 4, 9, [5], 3, 1...
2    [1, 6, [2], 2, 6, -1, 9, 5, [7, 8, 10], 8, 4, ...
3    [2, 7, [3], 2, 8, [3], 4, 10, [5], 8, 3, -1, 3...
4    [3, 8, -1, 4, 9, [5], 10, 4, [9], 9, 4, [10], ...
5    [6, 5, [8, 9, 10], 3, 8, [4, 5], 10, 3, [6, 9]...
6    [1, 7, [2, 4, 5], 3, 9, [1, 2, 4, 5], 8, 2, [6...
7    [8, 1, [6, 9, 10], 7, 4, [6, 8, 9, 10], 3, 9, ...
8    [7, 3, [6, 8, 9, 10], 5, 8, [1, 2, 4], 9, 5, [...
dtype: object

In [33]:
kill_log = []
for i in log:
    kill_log.extend(i[::3])

In [34]:
vict_log = []
for i in log:
    vict_log.extend(i[1::3])

In [35]:
assist_log = []
for i in log:
    assist_log.extend(i[2::3])

In [36]:
'|'.join(str(_) for _ in assist_log)

'-1|[4, 5]|-1|-1|[9]|-1|[7]|[3]|-1|[7, 8]|[6, 7]|[4]|[8]|[4, 5]|-1|[4, 5]|[3, 4]|-1|[4, 5]|[4, 5]|[5]|[1, 3, 5]|[6]|[2, 3]|[5]|-1|[10]|[7, 8]|[8, 10]|-1|[10]|[7]|[7, 10]|-1|[5]|[7, 10]|[2, 5]|-1|[8]|[6, 9]|[7, 9]|[8]|[6]|[9, 10]|[7, 9]|[5]|[2]|[5]|[7, 10]|[1]|-1|[5]|[7, 9, 10]|[7, 8, 10]|[3]|[7, 10]|[7, 9]|[2, 5]|[7, 10]|-1|[2, 5]|[9, 10]|[9, 10]|[9, 10]|[6]|-1|[5]|[9, 10]|[2, 3, 4]|[7, 8]|[10]|-1|[10]|-1|[1]|[10]|[10]|[9, 10]|[6, 10]|[9, 10]|[2]|-1|[7, 8, 10]|[7, 9, 10]|[5]|[7, 9, 10]|[2]|[8, 9]|[10]|[3]|[1, 5]|[8, 10]|-1|[1, 2, 5]|-1|[7]|[1, 2, 3, 5]|[7, 9, 10]|[6, 7, 10]|[6, 7, 9]|[7, 8, 9]|[10]|-1|[7, 9]|[1, 5]|[7, 9, 10]|[7, 9, 10]|-1|[2, 4, 5]|[6, 7]|[6, 7, 8]|[9, 10]|[6]|[3]|[3]|[5]|-1|-1|-1|[9]|[8]|[3]|[8]|[5]|-1|[2]|[2]|[9, 10]|[10]|[7, 9]|[2]|[2, 4]|[7, 9, 10]|[7, 8, 10]|[9, 10]|[8, 9, 10]|[7, 9, 10]|[6, 8, 10]|[6, 8, 10]|[1, 3, 4]|[4, 5]|[4, 5]|[9, 10]|[2, 3, 4, 5]|[6]|[6]|[6, 8, 10]|[1, 2, 3]|[6, 7, 10]|[1, 2, 4, 5]|[7, 8, 9]|[2, 3, 5]|[1, 5]|[3]|[2, 4, 5]|[2, 5]|[2, 4, 5]|

-------------------------------------------------------------------------------------

In [11]:
def log_lst_tmp(df):
    lst = []
    tmp = list(map(lambda x: x['events'], df.timelines['info']['frames']))
    for i in tmp:
        lst.extend(list(filter(lambda x: x['type'] == 'CHAMPION_KILL', i)))
    return lst

tmp_map = [element for array in tmp_map for elememt in array]

In [12]:
log_tmp = []
for i in range(len(df)):
    log_tmp.extend(log_lst_tmp(df.iloc[i]))

In [13]:
log_tmp

[{'bounty': 400,
  'killStreakLength': 0,
  'killerId': 6,
  'position': {'x': 6622, 'y': 7006},
  'shutdownBounty': 0,
  'timestamp': 243826,
  'type': 'CHAMPION_KILL',
  'victimDamageReceived': [{'basic': False,
    'magicDamage': 0,
    'name': 'Sett',
    'participantId': 6,
    'physicalDamage': 68,
    'spellName': 'sette',
    'spellSlot': 2,
    'trueDamage': 0,
    'type': 'OTHER'},
   {'basic': False,
    'magicDamage': 0,
    'name': 'Sett',
    'participantId': 6,
    'physicalDamage': 197,
    'spellName': 'settq',
    'spellSlot': 0,
    'trueDamage': 0,
    'type': 'OTHER'}],
  'victimId': 3},
 {'assistingParticipantIds': [4, 5],
  'bounty': 300,
  'killStreakLength': 0,
  'killerId': 2,
  'position': {'x': 13574, 'y': 2715},
  'shutdownBounty': 0,
  'timestamp': 297837,
  'type': 'CHAMPION_KILL',
  'victimDamageDealt': [{'basic': False,
    'magicDamage': 60,
    'name': 'Renata',
    'participantId': 5,
    'physicalDamage': 0,
    'spellName': 'renatae',
    'spellSlo

In [17]:
kill_lst = []
vict_lst = []
assist_lst = []
for i in log_tmp:
    kill_lst.append(str(i['killerId']))
    vict_lst.append(str(i['victimId']))
    str_tmp = ''
    try:
        for j in i['assistingParticipantIds']:
            str_tmp += (str(j)+' ')
        assist_lst.append(str_tmp)
    except:
        assist_lst.append('-1')

kill_lst = list(map(lambda x: x['killerId'], log_tmp))  
vict_lst = list(map(lambda x: x['victimId'], log_tmp))  

def assist_calc(x):  
    try:  
        return '.'.join(list(map(x['assistingParticipantIds'])))  
    except:  
        return ' '

assist_lst = list(map(lambda x: assist_calc(x), log_tmp))

In [30]:
def assist_calc(x):  
    try:  
        return '.'.join(list(map(x['assistingParticipantIds'])))  
    except:  
        return ' '

In [36]:
tmp_df = df.copy()
lst = []
for i in range(len(tmp_df)):
    g_id = tmp_df.iloc[i].gameid
    match = tmp_df.iloc[i].matchs['info']
    timeline = tmp_df.iloc[i].timelines['info']
    for j in range(10):
        lst_tmp = []
        lst_tmp.append(match['gameDuration'])
        lst_tmp.append(match['gameVersion'])
        lst_tmp.append(match['participants'][j]['summonerName'])
        lst_tmp.append(match['participants'][j]['participantId'])
        lst_tmp.append(match['participants'][j]['championName'])
        lst_tmp.append(match['participants'][j]['teamPosition'])
        lst_tmp.append(match['participants'][j]['teamId'])
        lst_tmp.append(match['participants'][j]['win'])
        lst_tmp.append(match['participants'][j]['kills'])
        lst_tmp.append(match['participants'][j]['deaths'])
        lst_tmp.append(match['participants'][j]['assists'])
        lst_tmp.append(match['participants'][j]['totalDamageDealtToChampions'])
        lst_tmp.append(match['participants'][j]['totalDamageTaken'])
        
        ban_blue = list(map(lambda x: str(x['championId']), match['teams'][0]['bans']))
        ban_red = list(map(lambda x: str(x['championId']), match['teams'][1]['bans']))
        ban_lst_tmp = list(set(ban_blue + ban_red))
        ban_lst = '|'.join(ban_lst_tmp)
        lst_tmp.append(ban_lst)
        kill_log = list(map(lambda x: list(filter(lambda y: y['type'] == 'CHAMPION_KILL', x['events'])), timeline['frames']))
        kill_log = [element for array in kill_log for element in array]
        k = list(map(lambda x: str(x['killerId']), kill_log))
        v = list(map(lambda x: str(x['victimId']), kill_log))
        a = list(map(assist_calc, kill_log))
        lst_tmp.append('|'.join(k))
        lst_tmp.append('|'.join(v))
        lst_tmp.append('|'.join(a))

In [37]:
lst_tmp

[1078,
 '12.12.450.4196',
 '호원동야생마',
 10,
 'Malphite',
 '',
 200,
 True,
 9,
 6,
 19,
 21277,
 18685,
 '',
 '7|5|9|3|9|8|2|5|5|5|7|8|7|7|7|1|7|9|6|10|10|9|3|5|5|2|10|10|9|7|3|6|10|10|9|9|3|7|5|5|5|7|6|10|6|9|8|10|5|9|3|3|6|1|6|6|5|3|5|5|7|8|9|1|1|3|1|2|2|5|8|7|7|9|8|3|10|2|5|1|5|7|8|6',
 '3|8|5|6|4|3|8|7|9|10|2|5|1|4|3|8|3|4|2|5|1|3|7|10|8|6|4|5|3|2|7|3|1|4|5|2|9|3|6|8|7|4|1|3|2|3|2|4|10|5|8|9|3|7|1|2|6|8|9|10|4|3|5|7|9|6|8|7|10|9|3|1|2|4|5|8|3|7|6|10|9|1|5|3',
 ' | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | | ']

miniproject 참고